#### An attempt to create BILSTM model which could be used for point wise and pairwise ranking.

In [1]:
from __future__ import print_function

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch import optim
from torch.utils.data import Dataset, DataLoader

import data_loader as dl
import os,json,pickle,time
import numpy as np

device = torch.device("cuda")

Using TensorFlow backend.


In [2]:
DEBUG = True

# if DEBUG:
#     print 'batch size is:', str(BATCH_SIZE), ' max length is:', str(MAX_LENGTH),' hidden size is:', str(HIDDEN_SIZE)

In [3]:
# LSTM encoder.
class Encoder(nn.Module):
    
    def __init__(self,max_length,hidden_dim,number_of_layer,embedding_dim,vocab_size,bidirectional,vectors=None):
        super(Encoder,self).__init__()
        
        self.max_length,self.hidden_dim,self.embedding_dim,self.vocab_size = max_length,hidden_dim,embedding_dim,vocab_size
        self.number_of_layer = number_of_layer
        self.bidirectional = bidirectional
        
        
        if vectors is not None:
            self.embedding_layer = nn.Embedding.from_pretrained(torch.FloatTensor(vectors))
            self.embedding_layer.weight.requires_grad = True
        else:
            # Embedding layer
            self.embedding_layer = nn.Embedding(self.vocab_size,self.embedding_dim)
        
        
        # LSTM layer
        self.lstm = nn.LSTM(self.embedding_dim,self.hidden_dim,self.number_of_layer,bidirectional = self.bidirectional)
        
    
    def init_hidden(self,batch_size,device):
        # Return a new hidden layer variable for LSTM
        # The axes semantics are (num_layers * num_directions, minibatch_size, hidden_dim)
        if not self.bidirectional:
            return (torch.zeros((self.number_of_layer,batch_size,self.hidden_dim),device=device),
                    torch.zeros((self.number_of_layer,batch_size,self.hidden_dim),device=device))
        else:
            return (torch.zeros((2*self.number_of_layer,batch_size,self.hidden_dim),device=device),
                    torch.zeros((2*self.number_of_layer,batch_size,self.hidden_dim),device=device))
    
    def forward(self,x,h):
        # x is the input and h is the hidden state.
        batch_size = x.shape[0]
        
        if DEBUG: print ("input/x shape is :", x.shape)
        if DEBUG: print ("hidden state shape is :", h[0].shape)
        
        x_embedded = self.embedding_layer(x)
        if DEBUG: print ("x_embedded transpose shape is :", x_embedded.transpose(1,0).shape)
            
#         output,h = self.lstm(x_embedded.view(-1,self.batch_size,self.embedding_dim),h)
        output,h = self.lstm(x_embedded.transpose(1,0),h)
        if DEBUG: print ("output shape is ",output.shape)
        if DEBUG: print ("h[0] shape is ", h[0].shape,"h[1] shape is ", h[1].shape)
        
        return output,h



In [4]:

MAX_LENGTH = 25
HIDDEN_SIZE = 10
BATCH_SIZE = 15
VOCAB_SIZE = 15000
EMBEDDING_DIM = 3

with torch.no_grad():
    print("testing encoder")
    dummy_input = torch.randint(0,VOCAB_SIZE-1,(MAX_LENGTH*BATCH_SIZE,),device=device).view(BATCH_SIZE,MAX_LENGTH).long()
    dummy_path = torch.randint(0,VOCAB_SIZE-1,(MAX_LENGTH*BATCH_SIZE,),device=device).view(BATCH_SIZE,MAX_LENGTH).long()
    encode = Encoder(MAX_LENGTH,HIDDEN_SIZE,5,EMBEDDING_DIM,VOCAB_SIZE,bidirectional=True).cuda(device)
    
    di_encoded,di_hidden = encode(dummy_input,encode.init_hidden(BATCH_SIZE,device))
    dp_encoded,dp_hidden = encode(dummy_path,encode.init_hidden(BATCH_SIZE,device))
    #di_encoded axes semantics = [MAX_LENGTH,BATCH_SIZE,2*Hidden_DIM]
    #reshaping to [BATCH_SIZE,MAX_LENGTH,2*HIDDEN_DIM]
    dot_product = torch.sum( di_encoded.view(BATCH_SIZE,MAX_LENGTH,-1)[:,-1,:]*dp_encoded.view(BATCH_SIZE,MAX_LENGTH,-1)[:,-1,:],-1)
    print(dot_product.shape)
#     dot = torch.bmm(di_encoded.view(BATCH_SIZE,MAX_LENGTH,-1),dp_encoded.view(BATCH_SIZE,MAX_LENGTH,-1))
#     print F.cosine_similarity(di_encoded,dp_encoded).shape
#     print torch.sum(torch.sum(dp_encoded.view(BATCH_SIZE,MAX_LENGTH,-1)*di_encoded.view(BATCH_SIZE,MAX_LENGTH,-1), -1),-1).shape


testing encoder
input/x shape is : torch.Size([15, 25])
hidden state shape is : torch.Size([10, 15, 10])
x_embedded transpose shape is : torch.Size([25, 15, 3])
output shape is  torch.Size([25, 15, 20])
h[0] shape is  torch.Size([10, 15, 10]) h[1] shape is  torch.Size([10, 15, 10])
input/x shape is : torch.Size([15, 25])
hidden state shape is : torch.Size([10, 15, 10])
x_embedded transpose shape is : torch.Size([25, 15, 3])
output shape is  torch.Size([25, 15, 20])
h[0] shape is  torch.Size([10, 15, 10]) h[1] shape is  torch.Size([10, 15, 10])
torch.Size([15])


In [5]:
MAX_LENGTH = 2
BATCH_SIZE = 3
HIDDEN_SIZE = 4

di_encoded = torch.tensor(np.arange(24).reshape((MAX_LENGTH, BATCH_SIZE, HIDDEN_SIZE)), dtype=torch.float)
dp_encoded = torch.randint(0,2,(MAX_LENGTH, BATCH_SIZE, HIDDEN_SIZE))


print(di_encoded, '\n', dp_encoded)
#BS,MA,HI

# print("dp_encoded.transpose(1,0) shape is \n ", dp_encoded.transpose(1,0)* di_encoded.transpose(1,0))
# a = dp_encoded.transpose(1,0)* di_encoded.transpose(1,0)
# b = 

print(di_encoded.view(BATCH_SIZE,MAX_LENGTH,-1).shape)
# dot_product_1 = torch.sum( di_encoded.view(BATCH_SIZE,MAX_LENGTH,-1)[:,-1,:]*dp_encoded.view(BATCH_SIZE,MAX_LENGTH,-1)[:,-1,:],-1)
# dot_product_2 = torch.(di_encoded.transpose(1,0)[:,-1,:]*dp_encoded.transpose(1,0)[:,-1,:],-1)
dot_product = torch.sum(torch.sum(dp_encoded.transpose(1,0)*di_encoded.transpose(1,0),1),1)
# print(dot_product_1)
print(dot_product)

tensor([[[  0.,   1.,   2.,   3.],
         [  4.,   5.,   6.,   7.],
         [  8.,   9.,  10.,  11.]],

        [[ 12.,  13.,  14.,  15.],
         [ 16.,  17.,  18.,  19.],
         [ 20.,  21.,  22.,  23.]]]) 
 tensor([[[ 0.,  0.,  1.,  0.],
         [ 1.,  0.,  1.,  0.],
         [ 1.,  1.,  1.,  0.]],

        [[ 1.,  1.,  1.,  1.],
         [ 0.,  1.,  0.,  0.],
         [ 0.,  1.,  1.,  0.]]])
torch.Size([3, 2, 4])
tensor([ 56.,  27.,  70.])


In [6]:
def load_relation():
    """
        Function used once to load the relations dictionary
        (which keeps the log of IDified relations, their uri and other things.)

    :param relation_file: str
    :return: dict
    """

    relations = pickle.load(open(os.path.join(COMMON_DATA_DIR, 'relations.pickle')))
    inverse_relations = {}
    for key in relations:
        value = relations[key]
        new_key = value[0]
        value[0] = key
        inverse_relations[new_key] = value

    return inverse_relations

In [7]:
COMMON_DATA_DIR = 'data/data/common'
_relations = load_relation()
_dataset = 'lcquad'
_dataset_specific_data_dir = 'data/data/lcquad/'
_model_specific_data_dir = 'data/data/core_chain_pairwise/lcquad/'
_file = 'id_big_data.json'
_max_sequence_length = 25
# _max_sequence_length = 15
_neg_paths_per_epoch_train = 5
_neg_paths_per_epoch_validation = 10
_training_split = .7
_validation_split = .8
_index = None

In [8]:
# _a = dl.load_data(_dataset, _dataset_specific_data_dir, _model_specific_data_dir, _file, _max_sequence_length,
#               _neg_paths_per_epoch_train,
#               _neg_paths_per_epoch_validation, _relations,
#               _index, _training_split, _validation_split, _model='core_chain_pairwise',_pairwise=True, _debug=True)
# train_questions, train_pos_paths, train_neg_paths, dummy_y_train, valid_questions, \
#                valid_pos_paths, valid_neg_paths, dummy_y_valid, test_questions, test_pos_paths, test_neg_paths = _a

# #Model specific paramters
# parameter_dict = {}
# parameter_dict['max_length'] = 25
# parameter_dict['hidden_size'] = 15
# parameter_dict['number_of_layer'] = 10
# parameter_dict['embedding_dim'] = 30
# parameter_dict['vocab_size'] = 15000
# parameter_dict['batch_size'] = 500
# parameter_dict['bidirectional'] = True
# parameter_dict['_neg_paths_per_epoch_train'] = 10
# parameter_dict['_neg_paths_per_epoch_validation'] = 1000
# parameter_dict['total_negative_samples'] = 1000
# parameter_dict['epochs'] = 2

# td = dl.TrainingDataGenerator(train_questions, train_pos_paths, train_neg_paths,
#                                                   _max_sequence_length, _neg_paths_per_epoch_train, BATCH_SIZE,10)
# trainLoader = DataLoader(td)

# vd = dl.ValidationDataset(train_questions, train_pos_paths, train_neg_paths,
#                                       parameter_dict['max_length'],
#                                       parameter_dict['_neg_paths_per_epoch_train'], parameter_dict['batch_size']
#                                       , parameter_dict['total_negative_samples'])
# validationLoader = DataLoader(vd)

# question_batch = ''
# pos_paths_batch = ''
# neg_paths_batch = ''
# for i_batch, sample_batched in enumerate(validationLoader):
#     question_batch =  sample_batched[0][0]
#     question_batch = np.reshape(question_batch,(-1,_max_sequence_length))
#     pos_paths_batch = np.reshape(sample_batched[0][1],(-1,_max_sequence_length))
#     neg_paths_batch = np.reshape(sample_batched[0][2],(-1,_max_sequence_length))
#     print pos_paths_batch.shape
#     print neg_paths_batch.shape
#     print question_batch.shape
#     break

# def validation_precision(questions,positive_paths,negative_paths):
#     #Assumption is that the number of negative paths are fixed.
#     for i in range(len(questions)):
#         question = np.repeat(question[i],len(negative_paths[i]))
#         paths = np.hstack((positive_paths[i],negative_paths[i]))
        
#     return 0

# question_batch = ''
# pos_paths_batch = ''
# neg_paths_batch = ''
# for i_batch, sample_batched in enumerate(trainLoader):
#     question_batch =  sample_batched[0][0]
#     question_batch = np.reshape(question_batch,(-1,_max_sequence_length))
#     pos_paths_batch = np.reshape(sample_batched[0][1],(-1,_max_sequence_length))
#     neg_paths_batch = np.reshape(sample_batched[0][2],(-1,_max_sequence_length))
#     break
# #     if 

# '''
#     arr_0 -> batch question
#     arr_1 -> batch_pos_path 
#     arr_2 -> batch_neg_paths
# '''
# question_batch = ''
# pos_paths_batch = ''
# neg_paths_batch = ''
# for i_batch, sample_batched in enumerate(trainLoader):
#     question_batch =  sample_batched[0][0]
#     question_batch = np.reshape(question_batch,(-1,_max_sequence_length))
#     pos_paths_batch = np.reshape(sample_batched[0][1],(-1,_max_sequence_length))
#     neg_paths_batch = np.reshape(sample_batched[0][2],(-1,_max_sequence_length))
#     break
# #     if i_batch == 1:
# #         print question_batch
# # #     print(i_batch, sample_batched['batch_questions'].size(),
# # #           sample_batched['batch_pos_paths'].size())

In [9]:
# with torch.no_grad():
#     print "testing encoder"
#     dummy_input = torch.randint(0,VOCAB_SIZE-1,(MAX_LENGTH*BATCH_SIZE,)).view(BATCH_SIZE,MAX_LENGTH).long()
#     dummy_path = torch.randint(0,VOCAB_SIZE-1,(MAX_LENGTH*BATCH_SIZE,)).view(BATCH_SIZE,MAX_LENGTH).long()
#     encode = Encoder(MAX_LENGTH,HIDDEN_SIZE,5,EMBEDDING_DIM,VOCAB_SIZE,BATCH_SIZE,bidirectional=True)
    
#     di_encoded,di_hidden = encode(dummy_input,encode.init_hidden())
#     dp_encoded,dp_hidden = encode(dummy_path,encode.init_hidden())
#     #di_encoded axes semantics = [MAX_LENGTH,BATCH_SIZE,2*Hidden_DIM]
#     #reshaping to [BATCH_SIZE,MAX_LENGTH,2*HIDDEN_DIM]
#     dot_product = torch.sum( di_encoded.view(BATCH_SIZE,MAX_LENGTH,-1)[:,-1,:]*dp_encoded.view(BATCH_SIZE,MAX_LENGTH,-1)[:,-1,:],-1)
#     print dot_product.shape

In [10]:
def validation_accuracy(valid_questions,valid_pos_paths,valid_neg_paths,model):
    precision = []
    with torch.no_grad():
        for i in range(len(valid_questions)):
            question = np.repeat(valid_questions[i].reshape(1,-1),len(valid_neg_paths[i])+1,axis=0) # +1 for positive path
            paths = np.vstack((valid_pos_paths[i].reshape(1,-1),valid_neg_paths[i]))
            
            hidden = model.init_hidden(question.shape[0],device)
            question = torch.tensor(question,dtype=torch.long,device = device)
            paths = torch.tensor(paths,dtype=torch.long,device=device)
            
            #Abstract out the predict
            question,_ = model(question.long(),hidden)
            paths,_ = model(paths.long(),hidden)
            score = torch.sum(question[-1]*paths[-1],-1)
#             score = torch.sum(torch.sum(question[-1].transpose(1,0)*paths[-1].transpose(1,0),1),1)
            arg_max = torch.argmax(score)
            if arg_max.item() == 0:# 0 is the positive path index
                precision.append(1)
            else:
                precision.append(0)
    return sum(precision)*1.0/len(precision)

In [11]:
# Function to save the model
def save_model(loc, model, model_name = 'model.torch' ,epochs=0, optimizer=None,accuracy = 0):
    """
        Input:
            loc: str of the folder where the models are to be saved - data/models/core_chain/cnn_dense_dense/lcquad/5'
            models: dict of 'model_name': model_object
            epochs, optimizers are int, torch.optims (discarded right now).
    """
    
    state = {
        'epoch':epochs,
        'optimizer':optimizer.state_dict(),
        'state_dict':model.state_dict(),
        'accuracy':accuracy
    }
    loc = loc + '/' + model_name
    print("model with accuracy ", accuracy,  "stored at", loc)
    torch.save(state, loc)

In [12]:
def save_location(problem,model_name,dataset):
    '''
            Location - data/models/problem/model_name/dataset/0X
            problem - core_chain
                    -intent
                    -rdf
                    -type_existence
            model_name - cnn_dense_dense ; pointwise_cnn_dense_dense ....
            
            dataset - 
            return a dir data/models/problem/model_name/dataset/0X
    '''
    #Check if the path exists or not. If not create one. 
    assert(problem in ['core_chain','intent','rdf','type_existence'])
    assert(dataset in ['qald','lcquad','transfer-a','transfer-b','transfer-c'])
    
    path = 'data/models/' + str(problem) + '/' + str(model_name) + '/' + str(dataset)
    if not os.path.exists(path):
        os.makedirs(path)
    path
    dir_name =  [int(name) for name in os.listdir(path+'/') ]
    if not dir_name:
        new_path_dir = path + '/' + str(0)
        os.mkdir(new_path_dir)
    else:
        dir_name = max(dir_name)
        new_model = dir_name+1
        new_path_dir = path + '/' + str(new_model)
        os.mkdir(new_path_dir)
    return new_path_dir

In [13]:
def train_bilstm_dot(ques_batch,pos_batch,neg_batch,dummy_y,model,optimizer,loss_fn,batch_size,max_sequence_length,device):
    '''
        :params ques_batch: batch of question
        :params pos_batch: batch of corresponding positive paths
        :params neg_batch: batch of corresponding negative paths
        :params dummy_y:a batch of ones (same length as that of batch)
    '''
    
    hidden = model.init_hidden(ques_batch.shape[0],device)
    optimizer.zero_grad()
    ques_batch, _ = model(ques_batch,hidden)
    pos_batch, _ = model(pos_batch,hidden)
    neg_batch, _ = model(neg_batch,hidden)
    pos_scores = torch.sum(ques_batch[-1]*pos_batch[-1],-1)
    neg_scores = torch.sum(ques_batch[-1]*neg_batch[-1],-1)
    '''
        If `y == 1` then it assumed the first input should be ranked higher
        (have a larger value) than the second input, and vice-versa for `y == -1`
    '''
    loss = loss_fn(pos_scores,neg_scores,dummy_y)
    loss.backward()
    optimizer.step()
    return loss

In [14]:
def training_loop(training_model,parameter_dict,data,dataset,device, problem = 'core_chain'):
    if training_model == 'bilstm_dot':
        # Find a location where model would be stored.
        model_save_location = save_location(problem,training_model,dataset)
        # model_save_locations - data/models/core_chain/cnn_dense_dense/lcquad/5
        
        #Model instantiation 
        encoder = Encoder(parameter_dict['max_length'],parameter_dict['hidden_size']
                         ,parameter_dict['number_of_layer'],parameter_dict['embedding_dim'],
                         parameter_dict['vocab_size'],
                         bidirectional=parameter_dict['bidirectional'],
                         vectors = data['vectors']).cuda(device)
        
        
        #Loading training data 
        td = dl.TrainingDataGenerator(data['train_questions'], data['train_pos_paths'], data['train_neg_paths'],
                                                  parameter_dict['max_length'], 
                                      parameter_dict['_neg_paths_per_epoch_train'], parameter_dict['batch_size']
                                      ,parameter_dict['total_negative_samples'])
        trainLoader = DataLoader(td)
        
        #dummy_y needed for calcualting loss
        dummy_y = torch.ones(parameter_dict['batch_size'],device=device)
        optimizer = optim.Adam(list(encoder.parameters()))
        max_margin_loss = nn.MarginRankingLoss(margin=1,size_average=False)
        train_loss = []
        test_loss = []
        valid_accuracy = []
        test_accuracy = []
        best_accuracy = 0
        try:
            for epoch in range(parameter_dict['epochs']):
                print("Epoch: ", epoch, "/", parameter_dict['epochs'])
                epoch_loss = []
                epoch_time = time.time()

                for i_batch, sample_batched in enumerate(trainLoader):
                    batch_time = time.time()
    #                 torch.tensor(train_P[sample_index], dtype=torch.long, device=device)
                    ques_batch = torch.tensor(np.reshape(sample_batched[0][0],(-1,parameter_dict['max_length'])), dtype=torch.long, device=device)
                    pos_batch =  torch.tensor(np.reshape(sample_batched[0][1],(-1,parameter_dict['max_length'])), dtype=torch.long, device=device)
                    neg_batch =  torch.tensor(np.reshape(sample_batched[0][2],(-1,parameter_dict['max_length'])), dtype=torch.long, device=device)

                    loss = train_bilstm_dot(ques_batch = ques_batch,
                                     pos_batch = pos_batch,
                                     neg_batch = neg_batch,
                                     dummy_y= dummy_y,
                                     model = encoder,
                                     optimizer=optimizer,
                                     loss_fn=max_margin_loss,
                                     batch_size=parameter_dict['batch_size'],
                                     max_sequence_length=parameter_dict['max_length'],
                                           device = device)
                    epoch_loss.append(loss.item())
    #                 print sum(epoch_loss,"  ",)
    #                 print(i_batch)
                    print("Batch:\t%d" % i_batch,"/%d\t: " % (parameter_dict['batch_size']),
                           "%s" % (time.time() - batch_time),
                           "\t%s" % (time.time() - epoch_time),
                         "\t%s" % (str(loss.item())),
                          end=None if i_batch+1 == int(int(i_batch)/parameter_dict['batch_size']) else "\n")
                print("Time taken in epoch: %s" % (time.time() - epoch_time))
                print("Training loss is : %s" % (sum(epoch_loss)))

                train_loss.append(sum(epoch_loss))

                if epoch%5 == 0:
                    #Calculating validation accuracy 
                    valid_accuracy.append(validation_accuracy(data['valid_questions'],data['valid_pos_paths'],
                                                          data['valid_neg_paths'],encoder))
                    #Calculating test accuracy  
                    test_accuracy.append(validation_accuracy(data['test_questions'],data['test_pos_paths'],
                                                          data['test_neg_paths'],encoder))

    #                 test_accuracy.append(0.0)

                    print("Validation accuracy is %s" % (valid_accuracy[-1]))
                    print("Test accuracy is %s" % (test_accuracy[-1]))
                    if valid_accuracy[-1] >= best_accuracy:
                        best_accuracy = valid_accuracy[-1]
                        save_model(model_save_location, encoder, model_name = 'encoder.torch' 
                                   ,epochs=epoch, optimizer=optimizer ,accuracy = best_accuracy)


            return train_loss,encoder, valid_accuracy, test_accuracy
        except KeyboardInterrupt:
            return train_loss,encoder, valid_accuracy, test_accuracy
                
                               

In [15]:
#Model specific paramters
parameter_dict = {}
parameter_dict['max_length'] = 25
parameter_dict['hidden_size'] = 128
parameter_dict['number_of_layer'] = 1
parameter_dict['embedding_dim'] = 300
parameter_dict['vocab_size'] = 15000
parameter_dict['batch_size'] = 500
parameter_dict['bidirectional'] = True
parameter_dict['_neg_paths_per_epoch_train'] = 100
parameter_dict['_neg_paths_per_epoch_validation'] = 1000
parameter_dict['total_negative_samples'] = 1000
parameter_dict['epochs'] = 300


#Data loading specific parameters
COMMON_DATA_DIR = 'data/data/common'
_relations = load_relation()
_dataset = 'lcquad'
_dataset_specific_data_dir = 'data/data/lcquad/'
_model_specific_data_dir = 'data/data/core_chain_pairwise/lcquad/'
_file = 'id_big_data.json'
_max_sequence_length = parameter_dict['max_length']
# _max_sequence_length = 15
_neg_paths_per_epoch_train = parameter_dict['_neg_paths_per_epoch_train']
_neg_paths_per_epoch_validation = parameter_dict['_neg_paths_per_epoch_validation']
_training_split = .7
_validation_split = .8
_index = None



_a = dl.load_data(_dataset, _dataset_specific_data_dir, _model_specific_data_dir, _file, _max_sequence_length,
              _neg_paths_per_epoch_train,  
              _neg_paths_per_epoch_validation, _relations,
              _index, _training_split, _validation_split, _model='core_chain_pairwise',_pairwise=True, _debug=True)
train_questions, train_pos_paths, train_neg_paths, dummy_y_train, valid_questions, \
               valid_pos_paths, valid_neg_paths, dummy_y_valid, test_questions, test_pos_paths, test_neg_paths,vectors = _a



(3500, 25)
(3500, 25)
(3500, 1000, 25)
(500, 25)
(500, 25)
(500, 1000, 25)


In [ ]:
DEBUG = False
data = {}
data['train_questions'] = train_questions
data['train_pos_paths'] = train_pos_paths
data['train_neg_paths'] = train_neg_paths
data['valid_questions'] = valid_questions
data['valid_pos_paths'] = valid_pos_paths
data['valid_neg_paths'] = valid_neg_paths
data['test_pos_paths'] = test_pos_paths
data['test_neg_paths'] = test_neg_paths
data['test_questions'] = test_questions
data['vectors'] = vectors

#training_model,parameter_dict,data,dataset,device, problem = 'core_chain'
training_loss,validation_accuracy,test_accuracy ,encoder = training_loop('bilstm_dot',parameter_dict,data,dataset='lcquad',device=device)

(3500, 25)
Epoch:  0 / 300
Batch:	0 /0	:  0.0573980808258 	0.0585141181946 	499.999938965
Batch:	1 /0	:  0.0560021400452 	0.115696191788 	499.996459961
Batch:	2 /0	:  0.0557200908661 	0.172681093216 	499.988006592
Batch:	3 /0	:  0.0551948547363 	0.229140043259 	499.831237793
Batch:	4 /0	:  0.0546600818634 	0.285100221634 	499.93560791
Batch:	5 /0	:  0.0534880161285 	0.339703083038 	499.882293701
Batch:	6 /0	:  0.0537719726562 	0.394305229187 	499.681610107
Batch:	7 /0	:  0.0574381351471 	0.452627182007 	499.41293335
Batch:	8 /0	:  0.0573461055756 	0.510861158371 	498.557434082
Batch:	9 /0	:  0.0543730258942 	0.565771102905 	496.848602295
Batch:	10 /0	:  0.0587010383606 	0.625298023224 	493.013183594
Batch:	11 /0	:  0.0515670776367 	0.677455186844 	486.245239258
Batch:	12 /0	:  0.054172039032 	0.732407093048 	469.011779785
Batch:	13 /0	:  0.0451958179474 	0.778447151184 	419.194702148
Batch:	14 /0	:  0.0393168926239 	0.818823099136 	377.972900391
Batch:	15 /0	:  0.0392880439758 	0.85913

Batch:	133 /0	:  0.0583679676056 	7.58391618729 	83.9867095947
Batch:	134 /0	:  0.0598311424255 	7.6447532177 	68.0163879395
Batch:	135 /0	:  0.0587799549103 	7.70446014404 	76.8060836792
Batch:	136 /0	:  0.0540549755096 	7.75923418999 	97.8774337769
Batch:	137 /0	:  0.0576188564301 	7.81760215759 	103.091918945
Batch:	138 /0	:  0.0529401302338 	7.87145900726 	107.849761963
Batch:	139 /0	:  0.057608127594 	7.93011808395 	70.3057556152
Batch:	140 /0	:  0.057853937149 	7.98888301849 	92.6567993164
Batch:	141 /0	:  0.0532331466675 	8.04296803474 	68.5459823608
Batch:	142 /0	:  0.0586178302765 	8.10252714157 	91.1028518677
Batch:	143 /0	:  0.0592949390411 	8.16293811798 	62.5780563354
Batch:	144 /0	:  0.0532670021057 	8.2171061039 	61.3682022095
Batch:	145 /0	:  0.0579769611359 	8.27612805367 	92.0727615356
Batch:	146 /0	:  0.0589139461517 	8.33567404747 	75.9133300781
Batch:	147 /0	:  0.0597159862518 	8.3966550827 	88.04246521
Batch:	148 /0	:  0.0583548545837 	8.456138134 	88.7049560547
B

Batch:	264 /0	:  0.0532121658325 	14.6436150074 	63.5514259338
Batch:	265 /0	:  0.0525989532471 	14.6973659992 	71.0493927002
Batch:	266 /0	:  0.0563669204712 	14.75583601 	55.2199859619
Batch:	267 /0	:  0.0538189411163 	14.81092906 	67.8328857422
Batch:	268 /0	:  0.0529279708862 	14.8647601604 	68.1319503784
Batch:	269 /0	:  0.0503327846527 	14.9162220955 	77.2049026489
Batch:	270 /0	:  0.0526349544525 	14.9692940712 	65.0739440918
Batch:	271 /0	:  0.0545420646667 	15.024559021 	54.910194397
Batch:	272 /0	:  0.0530600547791 	15.0782561302 	64.8996124268
Batch:	273 /0	:  0.0584480762482 	15.1373841763 	50.5357894897
Batch:	274 /0	:  0.0521171092987 	15.1902160645 	52.1426506042
Batch:	275 /0	:  0.0527391433716 	15.2436220646 	52.9105834961
Batch:	276 /0	:  0.0511829853058 	15.2956280708 	52.5622329712
Batch:	277 /0	:  0.0534620285034 	15.3500051498 	59.064239502
Batch:	278 /0	:  0.0590081214905 	15.4098491669 	73.7534790039
Batch:	279 /0	:  0.054162979126 	15.4650812149 	61.5972290039


Batch:	396 /0	:  0.051824092865 	21.7923750877 	40.493812561
Batch:	397 /0	:  0.0497839450836 	21.8432030678 	54.0731544495
Batch:	398 /0	:  0.0530140399933 	21.8972229958 	50.5982208252
Batch:	399 /0	:  0.0555830001831 	21.9537701607 	57.1153488159
Batch:	400 /0	:  0.054141998291 	22.0089490414 	74.262336731
Batch:	401 /0	:  0.0575721263885 	22.0676240921 	46.7994766235
Batch:	402 /0	:  0.0539510250092 	22.1225271225 	42.3228302002
Batch:	403 /0	:  0.0533080101013 	22.1767160892 	49.4286193848
Batch:	404 /0	:  0.058109998703 	22.2358231544 	46.9595451355
Batch:	405 /0	:  0.0533680915833 	22.2902460098 	54.5450744629
Batch:	406 /0	:  0.0587480068207 	22.349501133 	56.0774078369
Batch:	407 /0	:  0.0522041320801 	22.4026992321 	45.9415435791
Batch:	408 /0	:  0.0512101650238 	22.4547700882 	44.5483856201
Batch:	409 /0	:  0.0589020252228 	22.5146591663 	49.1270027161
Batch:	410 /0	:  0.0583839416504 	22.5741481781 	54.98960495
Batch:	411 /0	:  0.05806183815 	22.6331992149 	39.3623352051
Ba

Batch:	527 /1	:  0.0577847957611 	28.9026350975 	41.0085906982
Batch:	528 /1	:  0.0534400939941 	28.9569320679 	57.955291748
Batch:	529 /1	:  0.058305978775 	29.0159680843 	44.9848251343
Batch:	530 /1	:  0.0534131526947 	29.0702900887 	40.0119667053
Batch:	531 /1	:  0.0572571754456 	29.128385067 	60.1369628906
Batch:	532 /1	:  0.0547189712524 	29.184030056 	39.6695556641
Batch:	533 /1	:  0.0536341667175 	29.2383871078 	55.7281913757
Batch:	534 /1	:  0.0571529865265 	29.2964060307 	49.7675247192
Batch:	535 /1	:  0.0554020404816 	29.3525531292 	44.1645774841
Batch:	536 /1	:  0.0570290088654 	29.4106252193 	37.1456298828
Batch:	537 /1	:  0.0597651004791 	29.471280098 	41.5973472595
Batch:	538 /1	:  0.0517599582672 	29.5240650177 	40.6319656372
Batch:	539 /1	:  0.0516240596771 	29.5765380859 	41.9497680664
Batch:	540 /1	:  0.0583920478821 	29.635833025 	38.8605651855
Batch:	541 /1	:  0.0586521625519 	29.6953480244 	52.7804641724
Batch:	542 /1	:  0.0543248653412 	29.750619173 	50.4891738892

...

Batch:	227 /0	:  0.0535659790039 	12.634691 	0.0173110961914
Batch:	228 /0	:  0.0529398918152 	12.6887168884 	0.0
Batch:	229 /0	:  0.0517511367798 	12.7412970066 	0.0
Batch:	230 /0	:  0.0528237819672 	12.7949159145 	0.0
Batch:	231 /0	:  0.0559749603271 	12.8515779972 	0.0
Batch:	232 /0	:  0.0525691509247 	12.9050300121 	0.0
Batch:	233 /0	:  0.0545361042023 	12.9604020119 	0.0
Batch:	234 /0	:  0.0535070896149 	13.0147490501 	0.0
Batch:	235 /0	:  0.0522530078888 	13.0676589012 	0.0
Batch:	236 /0	:  0.0514540672302 	13.1201438904 	0.0
Batch:	237 /0	:  0.0527060031891 	13.1738009453 	0.0
Batch:	238 /0	:  0.0533318519592 	13.2281219959 	0.0
Batch:	239 /0	:  0.0554890632629 	13.2848320007 	0.0
Batch:	240 /0	:  0.0535168647766 	13.3394839764 	0.0
Batch:	241 /0	:  0.0479249954224 	13.3885159492 	0.0
Batch:	242 /0	:  0.0559010505676 	13.4454269409 	0.0
Batch:	243 /0	:  0.0523018836975 	13.4987909794 	0.0
Batch:	244 /0	:  0.0547208786011 	13.5545499325 	1.39337158203
Batch:	245 /0	:  0.053542137

Batch:	382 /0	:  0.0532569885254 	21.1760399342 	0.0
Batch:	383 /0	:  0.0535280704498 	21.2306780815 	0.0
Batch:	384 /0	:  0.0511989593506 	21.282752037 	0.0
Batch:	385 /0	:  0.052206993103 	21.335821867 	0.0
Batch:	386 /0	:  0.0519170761108 	21.3886060715 	0.0
Batch:	387 /0	:  0.0509989261627 	21.4407250881 	0.0
Batch:	388 /0	:  0.0518670082092 	21.49355793 	0.0
Batch:	389 /0	:  0.0547149181366 	21.54925704 	0.0
Batch:	390 /0	:  0.0528109073639 	21.6029500961 	0.329231262207
Batch:	391 /0	:  0.0585989952087 	21.6626770496 	0.0
Batch:	392 /0	:  0.0534198284149 	21.7171590328 	0.043083190918
Batch:	393 /0	:  0.0561649799347 	21.7743070126 	0.0
Batch:	394 /0	:  0.0549690723419 	21.8302080631 	0.0
Batch:	395 /0	:  0.052943944931 	21.8842380047 	0.0
Batch:	396 /0	:  0.0587708950043 	21.9440100193 	0.0
Batch:	397 /0	:  0.0556149482727 	22.0006430149 	0.0
Batch:	398 /0	:  0.0544230937958 	22.0560500622 	0.0
Batch:	399 /0	:  0.0576519966125 	22.1148610115 	0.17374420166
Batch:	400 /0	:  0.053

Batch:	536 /1	:  0.0545959472656 	29.7020158768 	0.0
Batch:	537 /1	:  0.0581059455872 	29.7608470917 	0.0
Batch:	538 /1	:  0.054899930954 	29.8163280487 	0.0
Batch:	539 /1	:  0.0542771816254 	29.8713879585 	0.0
Batch:	540 /1	:  0.0561180114746 	29.9281520844 	0.0
Batch:	541 /1	:  0.054044008255 	29.9829230309 	0.0
Batch:	542 /1	:  0.0596430301666 	30.0431680679 	0.0
Batch:	543 /1	:  0.0534720420837 	30.0973598957 	0.0
Batch:	544 /1	:  0.0584671497345 	30.1565098763 	0.0
Batch:	545 /1	:  0.0535719394684 	30.2108950615 	0.0
Batch:	546 /1	:  0.0585889816284 	30.2705280781 	0.0
Batch:	547 /1	:  0.0518178939819 	30.3229970932 	0.0
Batch:	548 /1	:  0.0551002025604 	30.3789670467 	0.0
Batch:	549 /1	:  0.0569939613342 	30.4375619888 	0.0
Batch:	550 /1	:  0.0537178516388 	30.4922208786 	0.0
Batch:	551 /1	:  0.0586190223694 	30.5519609451 	0.0
Batch:	552 /1	:  0.053426027298 	30.6061680317 	0.0
Batch:	553 /1	:  0.057991027832 	30.6651239395 	0.0
Batch:	554 /1	:  0.0589678287506 	30.7248649597 	0

Batch:	690 /1	:  0.0534729957581 	38.3633508682 	0.0
Batch:	691 /1	:  0.0538091659546 	38.4179370403 	0.0
Batch:	692 /1	:  0.053729057312 	38.4723689556 	0.0
Batch:	693 /1	:  0.0536308288574 	38.5270869732 	0.070497751236
Batch:	694 /1	:  0.0563361644745 	38.5841338634 	2.33602905273
Batch:	695 /1	:  0.0538599491119 	38.6391890049 	0.0
Batch:	696 /1	:  0.0550529956818 	38.6950790882 	0.0
Batch:	697 /1	:  0.0526740550995 	38.7486128807 	0.0
Batch:	698 /1	:  0.0549378395081 	38.8045749664 	0.0
Batch:	699 /1	:  0.0571000576019 	38.8627679348 	0.0
Time taken in epoch: 38.8632478714
Training loss is : 42.5427191257
Validation accuracy is 0.37
Test accuracy is 0.376
Epoch:  91 / 300
Batch:	0 /0	:  0.0649750232697 	0.0660190582275 	0.0
Batch:	1 /0	:  0.0617299079895 	0.128448009491 	1.55471801758
Batch:	2 /0	:  0.0594730377197 	0.188570022583 	0.0
Batch:	3 /0	:  0.0607841014862 	0.25001502037 	0.0
Batch:	4 /0	:  0.0555121898651 	0.306198120117 	0.0
Batch:	5 /0	:  0.0585360527039 	0.3653020858

Batch:	140 /0	:  0.0397500991821 	7.74849700928 	0.0
Batch:	141 /0	:  0.046945810318 	7.79609417915 	0.0
Batch:	142 /0	:  0.0605819225311 	7.8576540947 	0.0
Batch:	143 /0	:  0.0528728961945 	7.91153717041 	0.0
Batch:	144 /0	:  0.0581829547882 	7.97069907188 	0.0
Batch:	145 /0	:  0.0580489635468 	8.02973723412 	0.0
Batch:	146 /0	:  0.0521819591522 	8.08250617981 	0.0
Batch:	147 /0	:  0.0534908771515 	8.13694000244 	0.0
Batch:	148 /0	:  0.0530049800873 	8.19085621834 	0.0
Batch:	149 /0	:  0.0590989589691 	8.25106906891 	0.0
Batch:	150 /0	:  0.0549049377441 	8.30689406395 	0.51936340332
Batch:	151 /0	:  0.0576348304749 	8.3654282093 	3.08111000061
Batch:	152 /0	:  0.0539400577545 	8.42031812668 	0.0
Batch:	153 /0	:  0.0579149723053 	8.47914600372 	0.0
Batch:	154 /0	:  0.0594329833984 	8.53947210312 	0.0
Batch:	155 /0	:  0.0530548095703 	8.59346318245 	0.187780380249
Batch:	156 /0	:  0.0531640052795 	8.64761304855 	0.0
Batch:	157 /0	:  0.058718919754 	8.70738601685 	0.0
Batch:	158 /0	:  0.

In [ ]:
import matplotlib.pyplot as plt
import pylab
def visualize_loss(loss, loss2=None, _label="Some label", _label2="Some other label", _name="Generic Name", _only_epoch=True):
    """
        Fn to visualize loss.
        Expects either
            - [int, int] for epoch level stuff
            - [ [int, int], [int, int] ] for batch level data. 
    """
    
    plt.rcParams['figure.figsize'] = [15, 8] 
    
    # Detect input format
    if type(loss[0]) is not list: #in [int, float, long]:
        
#         print("here")
        plt.plot(loss, '-b', label=_label)
        if loss2: plt.plot(loss2, '-r', label=_label2)
        plt.ylabel(_name)
        pylab.legend(loc='upper left')
        plt.show()
        
    elif type(loss[0]) == list:
        
        if _only_epoch:
            loss = [ np.mean(x) for x in loss ]
            if loss2 is not None: 
                loss2 = [ np.mean(x) for x in loss2 ]
            
        else:
            loss = [ y for x in loss for y in x ]
            if loss2 is not None: loss2 = [ y for x in loss2 for y in x ]
            
        plt.plot(loss, '-b', label=_label)
        if loss2 is not None: plt.plot(loss2, '-r', label=_label2)
        plt.ylabel(_name)
        pylab.legend(loc='upper left')
        plt.show() 

In [ ]:
# precision = validation_accuracy(valid_questions,valid_pos_paths,valid_neg_paths,encoder)


print("Training Loss")
visualize_loss(loss=training_loss, _name="train loss", _only_epoch=True)


print("Validation Accuracy")
visualize_loss(loss=test_accuracy, _name="train loss", _only_epoch=True)

print("Testing Accuracy")
visualize_loss(loss=encoder, _name="train loss", _only_epoch=True)

In [ ]:
dummy_input_a = torch.randint(0,100,(500,25),device=device,dtype=torch.long)
dummy_input_b = torch.randint(0,100,(500,25),device=device,dtype=torch.long)
dummy_question = torch.randint(0,100,(500,25),device=device,dtype=torch.long)
loss_fun = nn.MarginRankingLoss(margin=1)
pos, _ = encode(dummy_input_a,encode.init_hidden(500,device))
neg, _ = encode(dummy_input_b,encode.init_hidden(500,device))
ques, _ = encode(dummy_question,encode.init_hidden(500,device))
print(pos[-1], '\n', neg[-1], '\n', ques[-1])
pos_score = torch.sum(ques[-1]*pos[-1],-1)
neg_score = torch.sum(ques[-1]*neg[-1],-1)


loss = loss_fun(pos_score,neg_score,-1*torch.ones(500,device=device))
print(loss)

In [ ]:
vocab= pickle.load(open('data/data/common/vocab.pickle'))
#reverse vocab it
reverse_vocab = {}
for keys in vocab:
    reverse_vocab[vocab[keys]] = keys

words = pickle.load(open('./resources/glove_vocab.pickle'))
reverse_words = {}
for keys in words:
    reverse_words[words[keys]] = keys

In [ ]:
q = train_questions[0]
rq = [reverse_vocab[x] for x in q]
print(rq)
print (words.keys()[:10])
wq = [reverse_words[x] for x in rq]
print(wq)
# Get glove texts

In [ ]:
# print(reverse_vocab[100])
for ques in train_pos_paths[0:2]:
    sent = []
    for q in ques:
        try:
            w = reverse_words[reverse_vocab[q]]
            if w != 'PAD':
                sent.append(w)
        except:
            sent.append('<unk>')
    print(" ".join(sent))

In [ ]:
def id_to_word(path,reverse_words,reverse_vocab,remove_pad = True):
    sent = []
    for q in path:
        try:
            w = reverse_words[reverse_vocab[q]]
            if w != 'PAD' and remove_pad:
                sent.append(w)
        except:
            sent.append('<unk>')
    return " ".join(sent)

In [ ]:
for ques in train_pos_paths[0:2]:
    print(id_to_word(ques,reverse_words,reverse_vocab))

In [ ]:
#Model specific paramters
parameter_dict = {}
parameter_dict['max_length'] = 25
parameter_dict['hidden_size'] = 128
parameter_dict['number_of_layer'] = 1
parameter_dict['embedding_dim'] = 300
parameter_dict['vocab_size'] = 15000
parameter_dict['batch_size'] = 3
parameter_dict['bidirectional'] = True
parameter_dict['_neg_paths_per_epoch_train'] = 10
parameter_dict['_neg_paths_per_epoch_validation'] = 1000
parameter_dict['total_negative_samples'] = 1000
parameter_dict['epochs'] = 100


td = dl.TrainingDataGenerator(data['train_questions'], data['train_pos_paths'], data['train_neg_paths'],
                                          parameter_dict['max_length'], 
                              parameter_dict['_neg_paths_per_epoch_train'], parameter_dict['batch_size']
                              ,parameter_dict['total_negative_samples'])
trainLoader = DataLoader(td)

In [ ]:
for i_batch, sample_batched in enumerate(trainLoader):
    ques_batch = np.reshape(sample_batched[0][0],(-1,parameter_dict['max_length']))
    pos_batch =  np.reshape(sample_batched[0][1],(-1,parameter_dict['max_length']))
    neg_batch =  np.reshape(sample_batched[0][2],(-1,parameter_dict['max_length']))
    for i in range(len(ques_batch)):
#         print(ques.tolist())
        print(id_to_word(ques_batch[i].tolist(),reverse_words,reverse_vocab))
        print(id_to_word(pos_batch[i].tolist(),reverse_words,reverse_vocab))
        print(id_to_word(neg_batch[i].tolist(),reverse_words,reverse_vocab))
    print("*******************")
    if i_batch == 10:
        break

In [ ]:

precision = []
for i in range(len(valid_questions)):
    print(id_to_word(valid_questions[i].tolist(),reverse_words,reverse_vocab))
    print(id_to_word(valid_pos_paths[i].tolist(),reverse_words,reverse_vocab))
    print(valid_pos_paths[i].shape)
    print(valid_neg_paths[i].shape)
#     for ques in valid_questions[i]:
#         print(id_to_word(ques.tolist(),reverse_words,reverse_vocab))
#     for ques in valid_pos_paths[i]:
#         print(id_to_word(ques.tolist(),reverse_words,reverse_vocab))
    for ques in valid_neg_paths[i]:
        print(id_to_word(ques.tolist(),reverse_words,reverse_vocab))
    break
    question = np.repeat(valid_questions[i].reshape(1,-1),len(valid_neg_paths[i])+1,axis=0) # +1 for positive path
    paths = np.vstack((valid_pos_paths[i].reshape(1,-1),valid_neg_paths[i]))

    hidden = model.init_hidden(question.shape[0],device)
    question = torch.tensor(question,dtype=torch.long,device = device)
    paths = torch.tensor(paths,dtype=torch.long,device=device)

    question,_ = model(question.long(),hidden)
    paths,_ = model(paths.long(),hidden)
    score = torch.sum(question[-1]*paths[-1],-1)
#             score = torch.sum(torch.sum(question[-1].transpose(1,0)*paths[-1].transpose(1,0),1),1)
    arg_max = torch.argmax(score)
    if arg_max.item() == 0:# 0 is the positive path index
        precision.append(1)
    else:
        precision.append(0)
#     return sum(precision)*1.0/len(precision)

In [ ]:
index = 3
print(id_to_word(valid_questions[index].tolist(),reverse_words,reverse_vocab))
print(id_to_word(valid_pos_paths[index].tolist(),reverse_words,reverse_vocab))
for ques in valid_neg_paths[index]:
    print(id_to_word(ques.tolist(),reverse_words,reverse_vocab))

In [ ]:
#Model specific paramters
parameter_dict = {}
parameter_dict['max_length'] = 25
parameter_dict['hidden_size'] = 128
parameter_dict['number_of_layer'] = 1
parameter_dict['embedding_dim'] = 300
parameter_dict['vocab_size'] = 15000
parameter_dict['batch_size'] = 500
parameter_dict['bidirectional'] = True
parameter_dict['_neg_paths_per_epoch_train'] = 10
parameter_dict['_neg_paths_per_epoch_validation'] = 1000
parameter_dict['total_negative_samples'] = 1000
parameter_dict['epochs'] = 100


td = dl.TrainingDataGenerator(data['train_questions'], data['train_pos_paths'], data['train_neg_paths'],
                                          parameter_dict['max_length'], 
                              parameter_dict['_neg_paths_per_epoch_train'], parameter_dict['batch_size']
                              ,parameter_dict['total_negative_samples'])
trainLoader = DataLoader(td)

In [ ]:
for i_batch, sample_batched in enumerate(trainLoader):
    ques_batch = np.reshape(sample_batched[0][0],(-1,parameter_dict['max_length']))
    pos_batch =  np.reshape(sample_batched[0][1],(-1,parameter_dict['max_length']))
    neg_batch =  np.reshape(sample_batched[0][2],(-1,parameter_dict['max_length']))
    print (ques_batch.shape)